# Example of use of ToxiFrench model

## Libraries

In [1]:
import torch
from transformers import AutoModelForCausalLM, AutoTokenizer, BitsAndBytesConfig
from peft import PeftModel
from rich.console import Console
from rich.panel import Panel
import os 

## Global settings and variables

In [2]:
# If you are using a proxy, set it up here (optional, you can comment these lines if not needed)
os.environ["HTTP_PROXY"] = "socks5h://127.0.0.1:1080"
os.environ["HTTPS_PROXY"] = "socks5h://127.0.0.1:1080"

# Choose which adapter to load
target_adapter_name = "rec" # Among the following six configurations : "odc", "oeb", "oec", "rdc", "reb", "rec"

# Load the base model
base_model_name = "Qwen/Qwen3-4B"

In [3]:
console = Console()

In [4]:
bnb_config = BitsAndBytesConfig(**{
            "load_in_4bit": True,
            "bnb_4bit_use_double_quant": True,
            "bnb_4bit_quant_type": "nf4",
            "bnb_4bit_compute_dtype": torch.float16
        })

## Load the model

In [5]:
tokenizer = AutoTokenizer.from_pretrained(
                base_model_name,
                use_fast=True,
                trust_remote_code=True
            )

if tokenizer.pad_token is None:
    tokenizer.pad_token = tokenizer.eos_token
    print("Tokenizer `pad_token` was None, set to `eos_token`.")

tokenizer.padding_side = 'left' 

In [6]:
model = AutoModelForCausalLM.from_pretrained(
                base_model_name,
                quantization_config=bnb_config,
                trust_remote_code=True,
                sliding_window=None,
            )
if model.generation_config.pad_token_id is None and tokenizer.pad_token_id is not None:
    model.generation_config.pad_token_id = tokenizer.pad_token_id
    print("Model `generation_config.pad_token_id` set from tokenizer.")

Loading checkpoint shards:   0%|          | 0/3 [00:00<?, ?it/s]

In [7]:
special_tokens_to_add = {
            "additional_special_tokens": [
            ]
        }
tokenizer.add_special_tokens(special_tokens_to_add)

model_embedding_size = model.get_input_embeddings().weight.size(0)
tokenizer_vocab_size = len(tokenizer)

if model_embedding_size != tokenizer_vocab_size:
    console.print(f"[yellow]Warning: Vocab size mismatch.[/yellow]"
          f"Model embeddings: {model_embedding_size}, "
          f"Tokenizer vocab: {tokenizer_vocab_size}")
    console.print("Resizing model token embeddings to match tokenizer...")
    model.resize_token_embeddings(tokenizer_vocab_size)

    # Verify the resize
    new_embedding_size = model.get_input_embeddings().weight.size(0)
    console.print(f"[bold green]Resized model embeddings to: {new_embedding_size}[/bold green]")
else:
    console.print("Model embedding size and tokenizer vocabulary size are already aligned.")

Warning: Vocab size mismatch.Model embeddings: 151936, Tokenizer vocab: 151669

Resizing model token embeddings to match tokenizer...

Resized model embeddings to: 151669

In [8]:
# Load the specific adapter by name from the repository
adapter_repo_id = "Naela00/ToxiFrench"
model = PeftModel.from_pretrained(
    model,
    adapter_repo_id,
    subfolder=target_adapter_name
)

print(f"Successfully loaded the '{target_adapter_name}' adapter!")

Successfully loaded the 'rec' adapter!


## Example of inference

In [9]:
prompt = "Message:\nputain mais elle est vraiment grand remplacée vot ville\n\nAnalyse:\n"
if "c" in target_adapter_name:
    prompt += "<think>\nExplication :\n"

In [10]:
max_new_tokens: int = 1024
do_sample: bool = True
temperature: float = 0.7
top_p: float = 0.9
top_k: int = 50
repetition_penalty: float = 1.1

In [11]:
inputs = tokenizer(
    prompt,
    return_tensors="pt",
    padding=True,
    truncation=True
).to(model.device)

default_generation_kwargs = {
    "max_new_tokens": max_new_tokens,
    "do_sample": do_sample,
    "temperature": temperature,
    "top_p": top_p,
    "top_k": top_k,
    "repetition_penalty": repetition_penalty,
    "eos_token_id": tokenizer.eos_token_id,
}

outputs = model.generate(**inputs, **default_generation_kwargs)
generated_text = tokenizer.decode(outputs[0], skip_special_tokens=False)

In [12]:
console.rule("[bold magenta]Model Output")
console.print('\n')
console.print(Panel.fit(generated_text, title="Generated Text", style="bold white on black"))

────────────────────────────────────────────────── Model Output ───────────────────────────────────────────────────

╭──────────────────────────────────────────────── Generated Text ─────────────────────────────────────────────────╮
│ Message:                                                                                                        │
│ putain mais elle est vraiment grand remplacée vot ville                                                         │
│                                                                                                                 │
│ Analyse:                                                                                                        │
│ <think>                                                                                                         │
│ Explication :                                                                                                   │
│ **Sujet du message :** Remplacement d'une personne dans une situation.                                          │
│                                                                                                                 │
│ **Résumé et explication :** L'auteur exprime son indignation ou sa surprise face à un remplacement, en          │
│ utilisant le terme "grand" qui pourrait indiquer une grande importance. Le contexte n'est pas précisé.          │
│ </think>                                                                                                        │
│ <think>                                                                                                         │
│ Tons :                                                                                                          │
│ Les tons perçus sont :                                                                                          │
│                                                                                                                 │
│ 1. **Indigné (certitude élevée)** - L'utilisation de « putain » montre une frustration claire face au           │
│ remplacement.                                                                                                   │
│ 2. **Surpris (certitude modérée)** - L'expression « mais elle est vraiment » suggère une surprise quant à la    │
│ situation.                                                                                                      │
│ 3. **Informel (certitude élevée)** - Le langage familier et l'absence de formalité renforcent ce ton.           │
│                                                                                                                 │
│ Doutes sur la signification exacte des termes, notamment « grand », pouvant indiquer une opinion personnelle.   │
│ </think>                                                                                                        │
│ <think>                                                                                                         │
│ Labels :                                                                                                        │
│ S0/H0/V0/R0/A0/I2                                                                                               │
│                                                                                                                 │
│ Justification :                                                                                                 │
│ Le message contient une vulgarité légère avec un ton informel, sans allusion sexuelle ni violence, et manifeste │
│ une critique moqueuse ou désapprobatrice sans intention hostile directe.                                        │
│ </think>                                                                                                        │
│ <think>                                                                                                         │
│ Score de toxicité :                                                                                             │
│ 4/10                                                  